# Práctica 2: SparkSQL TAREA 3

1. El primer objetivo de esta tarea es utilizar las funciones de la API para resolver las siguientes consultas:
    a. Lista de usuarios junto con el número de libros que han valorado 
    b. Rating máximo recibido por cada editorial
    c. Nombre del autor que ha recibido más ratings
    
2. El segundo objetivo de esta tarea es utilizar las Window Functions de Spark SQL para resolver las siguientes consultas:
    a. ¿Cuál es el título del libro con mayor número de ratings para cada editorial?
    b. ¿Cuál es la diferencia entre el número de ratings de cada libro y el número de ratings del libro con mayor número de ratings de la misma editorial?

In [1]:
# Vamos a trabajar con un conjunto de datos de Bookcrossing, con unos csv con datos de libros, puntuaciones y usuarios.
# realizamos imports necesarios
from pyspark.sql import Row
from pyspark.sql import functions as F

# cargamos los ficheros csv con los que vamos a trabajar, creando un DF para cada uno.
df_users = spark.read.format("csv").option("header", "true").option("sep", ";").load("BX-CSV-Dump/BX-Users.csv")
df_books = spark.read.format("csv").option("header", "true").option("sep", ";").load("BX-CSV-Dump/BX-Books.csv")
df_ratings = spark.read.format("csv").option("header", "true").option("sep", ";")\
                                    .load("BX-CSV-Dump/BX-Book-Ratings.csv")


In [2]:
# a. Lista de usuarios junto el número de libros que han valorado. 
# Agrupamos los datos de book_ratings por el id de usuario, y hacemos un count para obtener una columna donde vemos
# el id de usuario y la segunda columna el count con el recuento de ratings que ha hecho cada usuario. Mostramos todos
# los registros.
df_users_ratings = df_ratings.withColumnRenamed('User-ID','Usuario')
df_users_ratings.groupBy(["Usuario"]).count().show(df_users_ratings.count(),False)


+-------+-----+
|Usuario|count|
+-------+-----+
|277594 |1    |
|277840 |1    |
|278220 |2    |
|278659 |1    |
|1436   |12   |
|2136   |10   |
|3959   |2    |
|4032   |2    |
|4821   |3    |
|4937   |5    |
|5325   |1    |
|5925   |1    |
|6613   |1    |
|6731   |26   |
|7711   |1    |
|8433   |1    |
|9030   |1    |
|9583   |1    |
|9586   |2    |
|9993   |1    |
|10351  |10   |
|11078  |3    |
|12394  |1    |
|12529  |1    |
|13282  |1    |
|13442  |2    |
|13610  |1    |
|13865  |2    |
|14369  |1    |
|15634  |3    |
|16250  |1    |
|16504  |41   |
|16974  |7    |
|17427  |1    |
|17506  |1    |
|18333  |5    |
|18556  |3    |
|18634  |1    |
|18992  |1    |
|19132  |1    |
|19338  |1    |
|20219  |1    |
|20428  |11   |
|20512  |4    |
|21894  |2    |
|22121  |6    |
|22596  |1    |
|22728  |1    |
|23459  |16   |
|23843  |1    |
|23918  |1    |
|25032  |1    |
|25969  |2    |
|26082  |3    |
|26112  |3    |
|27108  |1    |
|27248  |1    |
|27317  |11   |
|28117  |1    |
|28135  

In [3]:
# b. Rating máximo por cada editorial. Hay que cruzar datos de dos DFs, el de Books donde están los datos de las
# distintas editoriales, y el de Ratings ya que es donde están las notas otorgadas a cada libro.
df_book_editorial = df_books.select(df_books.ISBN, df_books.Publisher)
df_book_rating = df_ratings.select(df_ratings.ISBN, 'Book-Rating')

# Para hacer el join cruzamos por el campo ISBN que tienen ambos DFs y corresponde al id de cada libro.
df_editorial_rating = df_book_editorial.join(df_book_rating, df_book_editorial.ISBN==df_book_rating.ISBN,'inner')\
                                        .drop(df_book_editorial.ISBN)

# El DF final se agrupa por editorial y para cada una se obtiene el rating máximo. Se muestran todos los registros,
# que será Editorial y la máxima puntuación recibida para cada una en alguno de sus libros.
df_final = df_editorial_rating.groupBy(["Publisher"]).agg(F.max("Book-Rating").alias("max_rating"))
df_final.show(df_final.count(),False)


+--------------------------------------------------------------------------------------------------------------------------------------+----------+
|Publisher                                                                                                                             |max_rating|
+--------------------------------------------------------------------------------------------------------------------------------------+----------+
|A. &amp; M. Muchnik                                                                                                                   |5         |
|Adams Media Corp                                                                                                                      |9         |
|Aqua Explorers                                                                                                                        |9         |
|Au diable Vauvert                                                                                              

In [4]:
# c. Nombre del autor que ha recibido más ratings. También hay que cruzar los datos de Books donde están los autores
# de los libros, y de Ratings para ver que autor ha recibido mayor número de valoraciones.
df_book_author = df_books.select(df_books.ISBN, 'Book-Author')
df_book_ratings = df_ratings.select(df_ratings.ISBN, 'Book-Rating')

# Ambos DFs se cruzan por el campo ISBN que identifica a un libro.
df_author_rating = df_book_author.join(df_book_ratings, df_book_author.ISBN==df_book_ratings.ISBN,'inner')\
                                        .drop(df_book_author.ISBN)

# El DF final se agrupa por el nombre del autor del libro, y para cada autor se hace un recuento del número de
# valoraciones que han recibido sus libros. Se ordena en orden descendente y se limita la salida a 1, y obtenemos
# que Stephen King es el autor que más valoraciones ha recibido.
df_final_author = df_author_rating.groupBy(["Book-Author"]).agg(F.count("Book-Rating").alias("Count"))
df_final_author.sort(df_final_author.Count.desc()).limit(1).show()


+------------+-----+
| Book-Author|Count|
+------------+-----+
|Stephen King|10053|
+------------+-----+



In [9]:
# Ahora utilizamos las functions windows de SparkSQL
# a. ¿Cuál es el título del libro con mayor número de ratings para cada editorial?.
from pyspark.sql.window import Window

# creamos un DF donde tengamos 3 columnas: Título del libro, Editorial y Número de ratings cruzando datos de 2
# de los dataframes de partida.
df_book_publisher = df_books.select(df_books.ISBN, 'Book-Title', df_books.Publisher)
df_book_ratings = df_ratings.select(df_ratings.ISBN, 'Book-Rating')
# Hacemos el join por el campo ISBN que comparten ambos dataframes
df_books_ratings = df_book_publisher.join(df_book_ratings, df_book_publisher.ISBN==df_book_ratings.ISBN,'inner')\
                                        .drop(df_book_publisher.ISBN)
# Se realiza el count de ratings para cada libro.
df_final = df_books_ratings.groupBy(["Book-Title", df_books_ratings.Publisher]).\
                                            agg(F.count("Book-Rating").alias("Ratings"))

# Una vez tenemos el DF con libros, editorial y número de ratings, calculamos la ventana indicando la partición con
# las filas incluidas en el marco y el ordenamiento de las mismas, para que sea descendente según el número de ratings.
overPublisher = Window.partitionBy('Publisher').orderBy(df_final.Ratings.desc())
# Generamos un DF con una columna rank donde se indica el ranking desde 1 a n de cada elemento en su grupo. Este 
# ranking indica el libro con más ratings en cada editorial.
ranked = df_final.withColumn('rank', F.dense_rank().over(overPublisher))

# Finalmente mostramos filtrado este DF, para mostrar sólo los libros que son el número 1 para cada editorial, o sea,
# el libro de cada editorial que tiene mayor número de ratings. Se muestran 200 registros para tener una visión del
# resultado.
ranked.where(ranked.rank == 1).show(200)


+--------------------+--------------------+-------+----+
|          Book-Title|           Publisher|Ratings|rank|
+--------------------+--------------------+-------+----+
|Comuna Verdad (An...| A. &amp; M. Muchnik|      1|   1|
|365 Tv-Free Activ...|    Adams Media Corp|     10|   1|
|Florida Shipwreck...|      Aqua Explorers|      1|   1|
|               Rihla|   Au diable Vauvert|      1|   1|
|Inseln der Südsee...|         Bertelsmann|      2|   1|
| Abenteuer der Ferne|         Bertelsmann|      2|   1|
|Eating in: From t...|     Biosphere Press|      1|   1|
|The mariner's tri...|   Blue Harbor Press|      1|   1|
| Spiritual midwifery|        Book Pub. Co|      2|   1|
|        Tofu cookery|        Book Pub. Co|      2|   1|
|Anyone Can Do It ...|            Capstone|      1|   1|
|The Learning Para...|            Capstone|      1|   1|
|Smart Things to K...|            Capstone|      1|   1|
|Endurance: Shackl...|Carroll &amp; Gra...|     41|   1|
|Creative Companio...|      Cel

In [8]:
# b. ¿Cuál es la diferencia entre el número de ratings de cada libro y el número de ratings del libro con mayor 
# número de ratings de la misma editorial?.
# Sobre el DF con título, editorial y número de ratings generado en la pregunta anterior, se añade un nueva columna
# para indicar la diferencia entre ratings de cada libro con el libro que tiene más ratings de su categoria. Esta
# columna con la diferencia se calcula con la resta entre el máximo de ratings de cada editorial menos el número
# de ratings de cada registro. En la salida se puede ver como para el libro de una editorial con más ratings la
# diferencia será 0 ya que él es el número 1 del ranking de dicha editorial, y luego el resto se va calculando la
# diferencia de ratings. 
# Por defecto se muestran 20 registros.
df_final.withColumn('Difer_Num_Ratings', F.max(df_final.Ratings).over(overPublisher) - df_final.Ratings).show(200)


+--------------------+--------------------+-------+-----------------+
|          Book-Title|           Publisher|Ratings|Difer_Num_Ratings|
+--------------------+--------------------+-------+-----------------+
|Comuna Verdad (An...| A. &amp; M. Muchnik|      1|                0|
|365 Tv-Free Activ...|    Adams Media Corp|     10|                0|
|The Verbally Abus...|    Adams Media Corp|      7|                3|
|Jacob Marley's Ch...|    Adams Media Corp|      4|                6|
|Show Biz Tricks f...|    Adams Media Corp|      4|                6|
|The Complete Sing...|    Adams Media Corp|      3|                7|
|Banned: Classical...|    Adams Media Corp|      2|                8|
| Mr. Cheap's Chicago|    Adams Media Corp|      2|                8|
|Knock 'Em Dead: T...|    Adams Media Corp|      2|                8|
|The Everything We...|    Adams Media Corp|      2|                8|
|Museum of Science...|    Adams Media Corp|      2|                8|
|Around the Americ..